# Automatic temporal resampling

## Load data

In [1]:
path = '../../../data/EIA/energy_generation_2024_preprocessed_us48.parquet'

In [2]:
import pandas as pd
df = pd.read_parquet(path).set_index('technology', append=True)['energy'].unstack('technology')
df

technology                 Battery storage     Coal  Geothermal    Hydro  \
period                                                                     
2023-12-31 19:00:00-05:00              NaN  88700.0         NaN  31141.0   
2023-12-31 20:00:00-05:00              NaN  88829.0         NaN  33318.0   
...                                    ...      ...         ...      ...   
2024-12-30 18:00:00-05:00            865.0  68842.0        35.0  33562.0   
2024-12-30 19:00:00-05:00           3140.0  74661.0        35.0  36721.0   

technology                 Natural Gas  Nuclear    Other  Petroleum  \
period                                                                
2023-12-31 19:00:00-05:00     194720.0  93973.0   9824.0      296.0   
2023-12-31 20:00:00-05:00     193932.0  94154.0  10545.0      299.0   
...                                ...      ...      ...        ...   
2024-12-30 18:00:00-05:00     165941.0  97439.0   1464.0      323.0   
2024-12-30 19:00:00-05:00     176563.0  97434.0   3205.0      320.0   

technology                 Pumped storage    Solar  \
period                                               
2023-12-31 19:00:00-05:00             NaN   7107.0   
2023-12-31 20:00:00-05:00             NaN   2417.0   
...                                   ...      ...   
2024-12-30 18:00:00-05:00           450.0  32835.0   
2024-12-30 19:00:00-05:00           169.0  17076.0   

technology                 Solar with integrated battery storage  Unknown  \
period                                                                      
2023-12-31 19:00:00-05:00                                    NaN      NaN   
2023-12-31 20:00:00-05:00                                    NaN      NaN   
...                                                          ...      ...   
2024-12-30 18:00:00-05:00                                    4.0      NaN   
2024-12-30 19:00:00-05:00                                    2.0      NaN   

technology                 Unknown energy storage     Wind  
period                                                      
2023-12-31 19:00:00-05:00                     NaN  36489.0  
2023-12-31 20:00:00-05:00                     NaN  41286.0  
...                                           ...      ...  
2024-12-30 18:00:00-05:00                  -151.0  63838.0  
2024-12-30 19:00:00-05:00                   -37.0  63008.0  

[8761 rows x 14 columns]

In [4]:
from modules import utils
utils.configure_plotly_template(showlegend=True)

In [5]:
df.plot()

In [6]:
df_base = df.copy()

## Steps

In [7]:
df = df_base.copy()

### Resample

In [8]:
r = df.resample('D').sum()
r

technology                 Battery storage       Coal  Geothermal     Hydro  \
period                                                                        
2023-12-31 00:00:00-05:00              0.0   420917.0         0.0  163544.0   
2024-01-01 00:00:00-05:00              0.0  2003526.0         0.0  658605.0   
...                                    ...        ...         ...       ...   
2024-12-29 00:00:00-05:00          12400.0  1672871.0       692.0  621785.0   
2024-12-30 00:00:00-05:00           8205.0  1283747.0       710.0  543202.0   

technology                 Natural Gas    Nuclear     Other  Petroleum  \
period                                                                   
2023-12-31 00:00:00-05:00     951321.0   470752.0   54838.0     1506.0   
2024-01-01 00:00:00-05:00    4461393.0  2251284.0  208803.0     7376.0   
...                                ...        ...       ...        ...   
2024-12-29 00:00:00-05:00    3644995.0  2329748.0  115220.0     7172.0   
2024-12-30 00:00:00-05:00    2836709.0  1948010.0   76357.0     6359.0   

technology                 Pumped storage     Solar  \
period                                                
2023-12-31 00:00:00-05:00             0.0   10407.0   
2024-01-01 00:00:00-05:00             0.0  286591.0   
...                                   ...       ...   
2024-12-29 00:00:00-05:00             0.0  361202.0   
2024-12-30 00:00:00-05:00           781.0  421435.0   

technology                 Solar with integrated battery storage  Unknown  \
period                                                                      
2023-12-31 00:00:00-05:00                                    0.0      0.0   
2024-01-01 00:00:00-05:00                                    0.0      0.0   
...                                                          ...      ...   
2024-12-29 00:00:00-05:00                                  129.0      0.0   
2024-12-30 00:00:00-05:00                                  103.0      0.0   

technology                 Unknown energy storage       Wind  
period                                                        
2023-12-31 00:00:00-05:00                     0.0   213099.0  
2024-01-01 00:00:00-05:00                     0.0   710888.0  
...                                           ...        ...  
2024-12-29 00:00:00-05:00                -12910.0  1099012.0  
2024-12-30 00:00:00-05:00                -12100.0  1404995.0  

[366 rows x 14 columns]

### Visualize

#### Plot

In [9]:
r.plot()

#### Heatmatrix

In [10]:
(r
 .div(1_000)
 .style
    .background_gradient(cmap='RdYlGn')
    .format(precision=2, thousands=',')
    .format_index(formatter=lambda x: x.strftime('%Y-%m-%dT%H'))
)

#### Heatmatrix with plotly

In [11]:
ranking = r.sum().sort_values(ascending=False).index.tolist()
r = r[ranking].T

r

period                  2023-12-31 00:00:00-05:00  2024-01-01 00:00:00-05:00  \
technology                                                                     
Natural Gas                              951321.0                  4461393.0   
Nuclear                                  470752.0                  2251284.0   
...                                           ...                        ...   
Unknown                                       0.0                        0.0   
Unknown energy storage                        0.0                        0.0   

period                  2024-01-02 00:00:00-05:00  2024-01-03 00:00:00-05:00  \
technology                                                                     
Natural Gas                             4922292.0                  5410997.0   
Nuclear                                 2237446.0                  2219168.0   
...                                           ...                        ...   
Unknown                                       0.0                        0.0   
Unknown energy storage                        0.0                        0.0   

period                  2024-01-04 00:00:00-05:00  2024-01-05 00:00:00-05:00  \
technology                                                                     
Natural Gas                             5096484.0                  4994398.0   
Nuclear                                 2225615.0                  2243366.0   
...                                           ...                        ...   
Unknown                                       0.0                        0.0   
Unknown energy storage                        0.0                        0.0   

period                  2024-01-06 00:00:00-05:00  2024-01-07 00:00:00-05:00  \
technology                                                                     
Natural Gas                             4726535.0                  4276493.0   
Nuclear                                 2266645.0                  2277191.0   
...                                           ...                        ...   
Unknown                                       0.0                        0.0   
Unknown energy storage                        0.0                        0.0   

period                  2024-01-08 00:00:00-05:00  2024-01-09 00:00:00-05:00  \
technology                                                                     
Natural Gas                             4451191.0                  4427893.0   
Nuclear                                 2266206.0                  2239781.0   
...                                           ...                        ...   
Unknown                                       0.0                        0.0   
Unknown energy storage                        0.0                        0.0   

period                  ...  2024-12-21 00:00:00-05:00  \
technology              ...                              
Natural Gas             ...                  4576611.0   
Nuclear                 ...                  2349236.0   
...                     ...                        ...   
Unknown                 ...                        0.0   
Unknown energy storage  ...                   -14275.0   

period                  2024-12-22 00:00:00-05:00  2024-12-23 00:00:00-05:00  \
technology                                                                     
Natural Gas                             4214473.0                  4415935.0   
Nuclear                                 2349581.0                  2345450.0   
...                                           ...                        ...   
Unknown                                       0.0                        0.0   
Unknown energy storage                   -12543.0                   -13315.0   

period                  2024-12-24 00:00:00-05:00  2024-12-25 00:00:00-05:00  \
technology                                                                     
Natural Gas                             4429252.0                  

In [12]:
import plotly.express as px
px.imshow(r)